This follows the blog post [here](https://blog.bytebytego.com/p/how-to-build-a-smart-chatbot-in-10?utm_source=substack&utm_medium=email).

The data comes from [here](https://abc.xyz/investor/previous/), although I didn't go through the trouble of also downloading all the transcripts.


This notebook requires three env vars to run:
- `OPENAI_API_KEY`
- `PINECONE_API_KEY`
- `PINECONE_ENV`

In [2]:
from langchain.document_loaders import DirectoryLoader

loader = DirectoryLoader(
    './data/', # my local directory
    glob='**/*.pdf',     # we only get pdfs
    show_progress=True
)
docs = loader.load()
docs

100%|██████████| 13/13 [03:11<00:00, 14.76s/it]


[Document(lc_kwargs={'page_content': 'UNITED STATES\n\nSECURITIES AND EXCHANGE COMMISSION Washington, D.C. 20549 ________________________________________________________________________________________\n\nFORM 10-Q\n\n(Mark One)\n\n________________________________________________________________________________________\n\n☒\n\n☐\n\nQUARTERLY REPORT PURSUANT TO SECTION 13 OR 15(d) OF THE SECURITIES EXCHANGE ACT OF 1934\n\nTRANSITION REPORT PURSUANT TO SECTION 13 OR 15(d) OF THE SECURITIES EXCHANGE ACT OF 1934\n\nFor the quarterly period ended March 31, 2020 OR\n\nFor the transition period from _______ to _______ Commission file number: 001-37580 ________________________________________________________________________________________\n\nAlphabet Inc.\n\n(Exact name of registrant as specified in its charter) ________________________________________________________________________________________\n\nDelaware\n\n61-1767919\n\n(State or other jurisdiction of incorporation or organization)\n\

In [3]:
from langchain.text_splitter import CharacterTextSplitter

text_splitter = CharacterTextSplitter(
    chunk_size=1000, 
    chunk_overlap=0
)
docs_split = text_splitter.split_documents(docs)
docs_split

Created a chunk of size 1113, which is longer than the specified 1000
Created a chunk of size 1658, which is longer than the specified 1000
Created a chunk of size 1155, which is longer than the specified 1000
Created a chunk of size 1163, which is longer than the specified 1000
Created a chunk of size 1074, which is longer than the specified 1000
Created a chunk of size 1150, which is longer than the specified 1000
Created a chunk of size 1121, which is longer than the specified 1000
Created a chunk of size 1043, which is longer than the specified 1000
Created a chunk of size 1148, which is longer than the specified 1000
Created a chunk of size 1891, which is longer than the specified 1000
Created a chunk of size 1229, which is longer than the specified 1000
Created a chunk of size 1233, which is longer than the specified 1000
Created a chunk of size 1009, which is longer than the specified 1000
Created a chunk of size 1128, which is longer than the specified 1000
Created a chunk of s

[Document(lc_kwargs={'page_content': 'UNITED STATES\n\nSECURITIES AND EXCHANGE COMMISSION Washington, D.C. 20549 ________________________________________________________________________________________\n\nFORM 10-Q\n\n(Mark One)\n\n________________________________________________________________________________________\n\n☒\n\n☐\n\nQUARTERLY REPORT PURSUANT TO SECTION 13 OR 15(d) OF THE SECURITIES EXCHANGE ACT OF 1934\n\nTRANSITION REPORT PURSUANT TO SECTION 13 OR 15(d) OF THE SECURITIES EXCHANGE ACT OF 1934\n\nFor the quarterly period ended March 31, 2020 OR\n\nFor the transition period from _______ to _______ Commission file number: 001-37580 ________________________________________________________________________________________\n\nAlphabet Inc.\n\n(Exact name of registrant as specified in its charter) ________________________________________________________________________________________\n\nDelaware\n\n61-1767919\n\n(State or other jurisdiction of incorporation or organization)\n\

In [25]:
?pinecone.init

Signature:
pinecone.init(
    api_key: str = None,
    host: str = None,
    environment: str = None,
    project_name: str = None,
    log_level: str = None,
    openapi_config: pinecone.core.client.configuration.Configuration = None,
    config: str = '~/.pinecone',
    **kwargs,
)
Docstring:
Initializes the Pinecone client.

:param api_key: Required if not set in config file or by environment variable ``PINECONE_API_KEY``.
:param host: Optional. Controller host.
:param environment: Optional. Deployment environment.
:param project_name: Optional. Pinecone project name. Overrides the value that is otherwise looked up and used from the Pinecone backend.
:param openapi_config: Optional. Set OpenAPI client configuration.
:param config: Optional. An INI configuration file.
:param log_level: Deprecated since v2.0.2 [Will be removed in v3.0.0]; use the standard logging module to manage logger "pinecone" instead.
File:      c:\users\ochseda2\miniconda3\envs\chatbot\lib\site-packages\pinecone

In [27]:
import pinecone 
from langchain.vectorstores import Pinecone
from langchain.embeddings.openai import OpenAIEmbeddings
import os

# we use the openAI embedding model
embeddings = OpenAIEmbeddings()
pinecone.init(
    api_key=os.environ['PINECONE_API_KEY'],
    environment=os.environ['PINECONE_ENV']
)

doc_db = Pinecone.from_documents(
    docs_split, 
    embeddings, 
    index_name='chatbotexample'
)

MaxRetryError: HTTPSConnectionPool(host='controller.us-west4-gcp-free.pinecone.io', port=443): Max retries exceeded with url: /databases (Caused by SSLError(SSLCertVerificationError(1, '[SSL: CERTIFICATE_VERIFY_FAILED] certificate verify failed: self-signed certificate in certificate chain (_ssl.c:1002)')))

In [26]:
os.environ['http_proxy'] = "http://proxy.novartis.net:2011"
os.environ['https_proxy'] = "https://proxy.novartis.net:2010"
os.environ["REQUESTS_CA_BUNDLE"] = "C:/Users/OCHSEDA2/certs/silverthree-chain.pem"
os.environ["SSL_CERT_FILE"] = "C:/Users/OCHSEDA2/certs/silverthree-chain.pem"

In [21]:
os.environ["REQUESTS_CA_BUNDLE"]

'C:/Users/OCHSEDA2/certs/silver_three.pem'